In [3]:
from pathlib import Path

import altair as alt
import pandas as pd
from IPython.display import display, HTML

In [4]:
save_figures = False
data_path = '../data/openzh-covid-19'

In [5]:
html_credits=HTML('''
<p style="font-size: smaller">Data Sources: 
  <a href="https://github.com/openZH/covid_19">OpenData Zuerich</a>,
  <a href="https://www.bfs.admin.ch">Federal Statistical Office</a>
<br>
Analysis:
  <a href="https://renkulab.io/projects/covid-19/covid-19-public-data">Covid-19 Public Data Collaboration Project</a>
</p>''')

## Summary data for Covid-19 cases in Switzerland

The data for Switzerland comes from the effort initiated by [OpenData Zürich](https://github.com/openZH/covid_19) and collected during the [Case data #covid19mon hackathon challenge](https://db.schoolofdata.ch/project/73). 

Below we make plots of total cases, total cases per 10k population and total deaths. You can click on the canton abbreviations in the legend to highlight individual lines. 

In [8]:
# read in cantonal data and produce one dataframe
df_list = []

for f in Path(data_path).glob('COVID19_Fallzahlen_Kanton_*total.csv'):
    df_list.append(pd.read_csv(f))

df = pd.concat(df_list)

df['date'] = pd.to_datetime(df['date'], dayfirst=True)

In [9]:
# read in population data
df_pop = pd.read_excel(
    Path(data_path) / '../ch-population-statistics/ch-population-by-age-canton.xls', 
    header=1, 
    skipfooter=5
)
df_pop = df_pop.where(
    df_pop.Region.str.startswith('-')
).dropna().sort_values('Region').reset_index(drop=True)

# match the cantons in the two datasets
df_pop['abbreviation_canton_and_fl'] = ['AG', 'AI', 'AR', 'BL', 'BS', 'BE', 'FR', 'GE', 'GL', 'GR', 'JU', 'LU', 'NE', 'NW', 'OW', 'SH', 'SZ', 'SO', 'SG', 'TG', 'TI', 'UR', 'VS', 'VD', 'ZG', 'ZH']

pop_d = df_pop[['abbreviation_canton_and_fl', 'Total']].set_index('abbreviation_canton_and_fl').to_dict()


# calculate cases and deaths per 10k

for x in ['conf', 'deceased']:
    df[f'ncumul_{x}_10k'] = df.apply(
        lambda row: row[f'ncumul_{x}']/pop_d['Total'][row.abbreviation_canton_and_fl]*10000, axis=1
    )

In [10]:
def generate_canton_chart(column, title, tooltip_title):
    """Produce a canton chart given a column name"""
    selection = alt.selection_multi(fields=['abbreviation_canton_and_fl'], bind='legend')
    chart = base.mark_line().encode(
        alt.X('date', title='Date'), 
        alt.Y(column, 
              title=title, scale=alt.Scale(type='linear')),
        color=alt.Color('abbreviation_canton_and_fl', legend=alt.Legend(title="Canton")),
        tooltip=[alt.Tooltip('abbreviation_canton_and_fl',title='Canton'),
                 alt.Tooltip(column,title=tooltip_title),
                 alt.Tooltip('date',title='Date')],
        opacity=alt.condition(selection, alt.value(1), alt.value(0.2))
    ).add_selection(
        selection
    )
    return chart

### Total cases

In [11]:
base = alt.Chart(df.where(df.ncumul_conf>0).dropna(subset=['abbreviation_canton_and_fl']))
base.configure_header(titleFontSize=25)
base.configure_axis(labelFontSize=15, titleFontSize=15)

cumul = generate_canton_chart('ncumul_conf', 'Cases', 'Cases')
cumul_10k = generate_canton_chart('ncumul_conf_10k', 'Cases per 10k population', 'Cases/10k')

chart = alt.hconcat(
    cumul, cumul_10k, title='Covid-19 cases in Switzerland by Canton'
).configure_title(
    anchor='middle'
)

display(chart)
if save_figures:
    chart.save(str(Path(figures_path) / 'switzerland-cases-by-canton.html'))
    
display(html_credits)

alt.HConcatChart(...)

### Deaths

In [12]:
base = alt.Chart(df.where(df.ncumul_deceased>0).dropna(subset=['abbreviation_canton_and_fl']))
base.configure_header(titleFontSize=25)
base.configure_axis(labelFontSize=15, titleFontSize=15)

deaths = generate_canton_chart('ncumul_deceased', 'Deaths', 'Deaths')
deaths_10k = generate_canton_chart('ncumul_deceased_10k', 'Deaths per 10k population', 'Deaths/10k')

chart = alt.hconcat(
    deaths, deaths_10k, title='Covid-19 deaths in Switzerland by Canton'
).configure_title(
    anchor='middle'
)
display(chart)    
display(html_credits)

if save_figures:
    chart.save(str(Path(figures_path) / 'switzerland-deaths-by-canton.html'))


alt.HConcatChart(...)